In [ ]:
!pip install deap
!pip install backtesting

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.metrics import r2_score,accuracy_score

In [ ]:
df = pd.read_csv('btc.csv')
df.head()

datetime      open      high       low     close      volume  \
0  2018-01-05 03:30:00  14797.89  14979.00  14601.00  14939.39  762.293702   
1  2018-01-05 04:30:00  14895.95  15100.08  14774.25  15059.54  892.734362   
2  2018-01-05 05:30:00  15059.56  15096.99  14802.00  14906.01  701.283048   
3  2018-01-05 06:30:00  14908.01  15100.00  14847.35  15040.00  922.722973   
4  2018-01-05 07:30:00  15038.04  15200.00  15038.04  15098.11  985.850712   

            ma7          ma21        rsi    upper_band  ...           sar  \
0  14765.905714  14693.307619  73.523748  15257.286699  ...  14099.125535   
1  14850.130000  14687.946667  74.235674  15234.686704  ...  14153.838003   
2  14886.861429  14678.190000  64.976108  15199.972788  ...  14229.537363   
3  14919.575714  14674.381905  65.475151  15183.639947  ...  14299.180774   
4  14948.564286  14685.001429  72.807464  15220.465386  ...  14363.252712   

          cci          vwap            efi         ema14         ema21  \
0   97.185359  14716.686419  107872.181770  14713.969375  14701.809507   
1  119.808224  14723.722367  107262.033594  14760.045459  14734.330461   
2   89.589687  14728.099258 -107667.986359  14779.507397  14749.937692   
3   95.183741  14735.202120  123635.651152  14814.239744  14776.306992   
4  119.877560  14745.591170   57287.784874  14852.089112  14805.561811   

         adx  diff_close  classi  Next_close  
0  46.365497      120.15       1    15059.54  
1  45.076379     -153.53       0    14906.01  
2  43.848079      133.99       1    15040.00  
3  42.071915       58.11       1    15098.11  
4  41.339725     -132.74       0    14965.37  

[5 rows x 28 columns]

In [ ]:
df['Open'] = df['open']
df['Close'] = df['close']
df['High'] = df['high']
df['Low'] = df['low']
df['Volume'] = df['volume']

df.index = pd.to_datetime(df['datetime'])
df.drop(['open','high','low','close'], axis=1,inplace=True)

In [ ]:
split_index = int(len(df) * 0.8)

first_80_percent = df.iloc[:split_index]
last_20_percent = df.iloc[split_index:]

In [ ]:
X_train = first_80_percent[['Open', 'High', 'Low', 'Close', 'Volume', 'ma7', 'ma21',
       'rsi', 'upper_band', 'lower_band', 'ao', 'macd', 'signal_line',
       'choppiness_index', 'slowk', 'slowd', 'atr', 'sar', 'cci', 'vwap',
       'efi', 'ema14', 'ema21', 'adx']]
X_test = last_20_percent[['Open', 'High', 'Low', 'Close', 'Volume', 'ma7', 'ma21',
       'rsi', 'upper_band', 'lower_band', 'ao', 'macd', 'signal_line',
       'choppiness_index', 'slowk', 'slowd', 'atr', 'sar', 'cci', 'vwap',
       'efi', 'ema14', 'ema21', 'adx']]

In [ ]:
y_class_train = first_80_percent['classi']
y_class_test = last_20_percent['classi']

In [ ]:
from sklearn.ensemble import RandomForestClassifier

rfc_model = RandomForestClassifier(max_depth=5,
                                   min_samples_leaf=2,
                                   min_samples_split=10,
                                   random_state=42)
rfc_model.fit(X_train,y_class_train)
y_pred_m4 = rfc_model.predict(X_test)
accuracy_score(y_class_test,y_pred_m4)

0.5375966268446943

In [ ]:
from xgboost import XGBClassifier

xgb_model = XGBClassifier(learning_rate=0.01,
                          max_depth=3,
                          n_estimators=300,
                          random_state=42)
xgb_model.fit(X_train,y_class_train)
y_pred_m5 = xgb_model.predict(X_test)
accuracy_score(y_class_test,y_pred_m5)

0.5318341531974702

In [ ]:
from sklearn.ensemble import StackingClassifier
from sklearn.svm import SVC

estimators = [('rf',rfc_model),('xgb',xgb_model)]
stacked_model1 = StackingClassifier(estimators,final_estimator=SVC(),n_jobs=-1)
stacked_model1.fit(X_train,y_class_train)
y_pred_sm1 = stacked_model1.predict(X_test)
accuracy_score(y_class_test,y_pred_sm1)

0.5295853829936753

In [ ]:
from backtesting import Strategy
from backtesting.lib import crossover, TrailingStrategy

/usr/local/lib/python3.10/dist-packages/backtesting/_plotting.py:50: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


In [ ]:
def PREDS_RFC(model,X):
  return pd.Series(model.predict(X))
def PREDS_XGB(model,X):
  return pd.Series(model.predict(X))

In [ ]:
def MACD(df,lb_fast,lb_slow,lb_sig):
  lb_fast = int(lb_fast)
  lb_slow = int(lb_slow)
  lb_sig = int(lb_sig)
  ema_fast = df['Close'].ewm(span=lb_fast).mean()
  ema_slow = df['Close'].ewm(span=lb_slow).mean()
  macd = ema_fast - ema_slow
  return np.array(macd)

def MACDSignal(df,lb_fast,lb_slow,lb_sig):
  lb_fast = int(lb_fast)
  lb_slow = int(lb_slow)
  lb_sig = int(lb_sig)
  ema_fast = df['Close'].ewm(span=lb_fast).mean()
  ema_slow = df['Close'].ewm(span=lb_slow).mean()
  macd = ema_fast - ema_slow
  signal = macd.ewm(span=lb_sig).mean()
  return np.array(signal)

In [ ]:
class MLStrategy(TrailingStrategy,Strategy):
  df = df
  model = rfc_model
  X = X_test
  lb_fast = 14
  lb_slow = 26
  lb_sig = 12

  def init(self):
    super().init()
    self.forecasts1 = self.I(PREDS_RFC,self.model,self.X)
    self.macd = self.I(MACD,self.X,self.lb_fast,self.lb_slow,self.lb_sig)
    self.signal = self.I(MACDSignal,self.X,self.lb_fast,self.lb_slow,self.lb_sig)
    self.set_atr_periods(100)
    self.set_trailing_sl(n_atr=1)

  def next(self):
    super().next()

    if self.forecasts1 > 0.5 and crossover(self.macd,self.signal):
        self.position.close()
        self.buy()

    elif self.forecasts1 < 0.5 and crossover(self.signal,self.macd):
        self.position.close()
        self.sell()

In [ ]:
from backtesting import Backtest

bt = Backtest(X_test, MLStrategy, cash=100_000, commission=0.0015)
stats = bt.run()
stats

Start                     2021-04-09 08:30:00
End                       2022-01-31 05:30:00
Duration                    296 days 21:00:00
Exposure Time [%]                    5.973296
Equity Final [$]                 81851.640025
Equity Peak [$]                 100231.903445
Return [%]                          -18.14836
Buy & Hold Return [%]              -36.485558
Return (Ann.) [%]                  -21.752019
Volatility (Ann.) [%]                8.773858
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -18.337738
Avg. Drawdown [%]                   -6.864162
Max. Drawdown Duration      281 days 04:00:00
Avg. Drawdown Duration       97 days 20:00:00
# Trades                                   73
Win Rate [%]                        30.136986
Best Trade [%]                       7.271904
Worst Trade [%]                     -5.681627
Avg. Trade [%]                    

In [ ]:
import random
from deap import base, creator, tools, algorithms

creator.create('FitnessMulti', base.Fitness, weights=(1.0,1.0,1.0,1.0,1.0))
# (Maximize Win Rate [%], Maximize Return [%], Maximize Sharpe Ratio, Maximize # Trades, Maximize Max. Drawdown -> since we are taking it as -ve)
creator.create('Individual', list, fitness=creator.FitnessMulti)

In [ ]:
toolbox = base.Toolbox()
toolbox.register('rand_lookb', random.randint, 1, 90)
toolbox.register('individual', tools.initCycle, creator.Individual, (toolbox.rand_lookb,
                                                                     toolbox.rand_lookb,
                                                                     toolbox.rand_lookb,)
                                                                     ,n=1)

In [ ]:
def evaluate(individual):
  stats = bt.optimize(lb_fast=[individual[0]],
                    lb_slow=[individual[1]],
                    lb_sig=[individual[2]])
  return stats['Win Rate [%]'],stats['Return [%]'],stats['Sharpe Ratio'],stats['# Trades'],stats['Max. Drawdown [%]']

In [ ]:
toolbox.register('evaluate', evaluate)
toolbox.register('mate', tools.cxSimulatedBinary, eta=20)
toolbox.register('mutate', tools.mutPolynomialBounded, low=1, up=90, eta=20, indpb=1.0/9)
toolbox.register('selectNSGA', tools.selNSGA2)
toolbox.register('selectSPEA', tools.selSPEA2)
toolbox.register('selectBest', tools.selBest)

toolbox.register('population', tools.initRepeat, list, toolbox.individual)

In [ ]:
population = toolbox.population(n=100)

fitnesses = list(map(toolbox.evaluate, population))
for ind, fit in zip(population, fitnesses):
    ind.fitness.values = fit

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

...

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
fronts_initial = tools.sortNondominated(population, len(population), first_front_only=True)[0]
for i, ind in enumerate(fronts_initial):
    print(f"Individual {i + 1} - Objectives: {ind.fitness.values}")

Individual 1 - Objectives: (30.76923076923077, -12.811398915000014, 0.0, 169.0, -19.958727435264436)
Individual 2 - Objectives: (38.80597014925373, 1.4313494849999988, 0.17058381213538693, 67.0, -9.654439850161001)
Individual 3 - Objectives: (41.86440677966102, -36.656407040000474, 0.0, 590.0, -40.30016690971)
Individual 4 - Objectives: (48.148148148148145, 3.8822010549999106, 0.6551385728268829, 27.0, -5.276234997386997)
Individual 5 - Objectives: (nan, 0.0, nan, 0.0, -0.0)
Individual 6 - Objectives: (33.9622641509434, -15.55579666499997, 0.0, 212.0, -28.133424462950096)
Individual 7 - Objectives: (38.46153846153847, 4.697901060000033, 0.3615062817287255, 39.0, -11.713244932423294)
Individual 8 - Objectives: (40.909090909090914, 2.7598994099999543, 0.6168310898256045, 22.0, -3.4525745024779453)
Individual 9 - Objectives: (33.84615384615385, 4.991734839999903, 0.5102172521648546, 65.0, -7.054242203001282)
Individual 10 - Objectives: (33.33333333333333, -1.984943565000125, 0.0, 69.0, -1

In [ ]:
def feasible(individual):
  if(individual[0]<1 or individual[1]<1 or individual[2]<1):
    return False
  return True

In [ ]:
import warnings
warnings.filterwarnings("ignore")
from tqdm.auto import tqdm
pop = population.copy()
# Configure the algorithm
NGEN = 100
MU = 40
LAMBDA = 1000
CXPB = 0.9
MUTPB = 1.0/len(population)

for g in tqdm(range(NGEN)):
    population1 = toolbox.selectNSGA(population,MU)
    population2 = toolbox.selectSPEA(population,MU)
    population = population1+population2

    offspring = algorithms.varAnd(population,toolbox,cxpb=CXPB,mutpb=MUTPB)

    offspring = list(filter(feasible,offspring))
    invalid_ind = [ind for ind in offspring if not ind.fitness.valid]
    fitnesses = toolbox.map(toolbox.evaluate, invalid_ind)
    for ind, fit in zip(invalid_ind, fitnesses):
        ind.fitness.values = fit

    population = toolbox.selectBest(offspring,100,fit_attr='fitness')

  0%|          | 0/100 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

...

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

Backtest.optimize:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
fronts_final = tools.sortNondominated(population, len(population), first_front_only=True)[0]
for i, ind in enumerate(fronts_final):
    print(f"Individual {i + 1} - Objectives: {ind.fitness.values}")

In [ ]:
for i, ind in enumerate(fronts_final):
    print(f"Individual {i + 1} : {ind}")

In [ ]:
stats = bt.optimize(lb_fast=[14],
                    lb_slow=[46],
                    lb_sig=[55])
stats